<CENTER>
</br>
<p><font size="5">  M2MO & EY - Internship </font></p>
<p><font size="5">  Modelling Initial Margin and Counterparty Risk in Uncleared Derivatives </font></p>
<p><font size="4">  SANGLIER Nathan </font></p>
<p><font size="3"></br>May 2025</font></br></div>
<p><span style="color:blue">nathan.sanglier@etu.u-paris.fr</span>
</p>
</CENTER>

In this notebook, we analyze if our approximated analytical formula for the value-at-risk of a swaption in the one factor Hull-White model is coherent. More precisely, we need to check that $z \mapsto w_i(z)$ is strictly monotonic for most of values $z$ drawn from a standard Gaussian distribution. Notice that $u(t, \cdot)$ being strictly monotonic is a necessary and sufficient condition.

## <span id="section-0" style="color:#00B8DE"> 0 - Imports & Parameters </span>

In [65]:
import  numpy                   as      np
import  matplotlib.pyplot       as      plt
import  matplotlib.animation    as      animation
from    scipy.stats             import  norm
from    utils                   import  TimeGrid
from    pricing_models          import  YieldCurve, OneFactorHullWhite
from    pricing_engines         import  SwaptionOneFactorHullWhite
from    IPython.display         import  HTML

In [66]:
np.random.seed(0)

In [ ]:
num_paths   = 100
maturity    = 1
time_grid   = TimeGrid(1/240, maturity)
alpha       = 0.99
mpor        = 1/24

## <span id="section-0" style="color:#00B8DE"> I - Analysis with default swaption and HW1F parameters </span>

Here, we analyze if $u(t, \cdot)$ is strictly monotonic for the swaption and one-factor Hull-White parameters values of our case study (ie. not too extreme).

In [ ]:
risk_factor = OneFactorHullWhite(0.01, 0.015, YieldCurve(0.05, -0.03, -0.18))
portfolio   = SwaptionOneFactorHullWhite(maturity, 0.04, TimeGrid(0.25, 4.75), 10000, risk_factor)
risk_factor.set_time_grid(time_grid)
risk_factor_vals = np.linspace(-0.2, 0.2, num_paths)
risk_factor_paths = np.repeat(risk_factor_vals.reshape(-1, 1), len(time_grid.grid), axis=1)
mtm_paths = portfolio.generate_paths(risk_factor_paths)

In [68]:
def risk_factor_mean(t, risk_factor):
    return risk_factor.spot*np.exp(-risk_factor.mean_reversion_speed*t) + risk_factor.beta(t) -  risk_factor.beta(0)*np.exp(-risk_factor.mean_reversion_speed*t)

def risk_factor_variance(t, risk_factor):
    return (risk_factor.volatility**2 / (2*risk_factor.mean_reversion_speed)) * (1 - np.exp(-2*risk_factor.mean_reversion_speed*t))

risk_factor_pdf_vals        = np.zeros((num_paths, len(time_grid.grid)))
risk_factor_pdf_vals[:, 1:] = norm.pdf(risk_factor_vals, loc=risk_factor_mean(time_grid.grid[1:], risk_factor).reshape(-1, 1), scale=np.sqrt(risk_factor_variance(time_grid.grid[1:], risk_factor)).reshape(-1, 1)).T
risk_factor_pdf_vals[:, 0]  = 0

In [87]:
plt.close('all')
fig, ax = plt.subplots(1, 1, figsize=(8, 4))
u = ax.plot(risk_factor_vals, mtm_paths[:, 0], label='$u(t, r)$')[0]
v = ax.plot(risk_factor_vals, risk_factor_pdf_vals[:, 0], label='pdf of $r_t$')[0]
rtime_grid = time_grid.grid[::2]
rmtm_paths = mtm_paths[:, ::2]
rpdf_vals = risk_factor_pdf_vals[:, ::2] * 10
ax.set_title(f"t = {rtime_grid[0]:.2f}")
ax.grid()
ax.set_xlabel("$r$")
ax.set_ylim(np.min(rmtm_paths), np.max(rmtm_paths))
ax.legend(loc='upper left')
plt.tight_layout()


def update(n):
    u.set_ydata(rmtm_paths[:, n])
    v.set_ydata(rpdf_vals[:, n] * 10)
    ax.set_title(f"t = {rtime_grid[n]:.2f}")
    return [u]

video = animation.FuncAnimation(fig, update, frames=len(rtime_grid), blit=True, interval=100, repeat=False)
plt.close(fig)
HTML(video.to_jshtml())

## <span id="section-0" style="color:#00B8DE"> II - Analysis with other parameters </span>

Here, you can test for other parameters. We have tried several combinations (including more extreme values) and it always yields a strictly monotonic function. Notice that the function is strictly increasing, but may be decreasing depending on the sign of constants $C_1, C_2, C_3$ in the yield curve definition.

In [83]:
risk_factor = OneFactorHullWhite(0.09, 0.055, YieldCurve(-0.03, 0.02, 0.03))
portfolio   = SwaptionOneFactorHullWhite(maturity, 0.04, TimeGrid(0.25, 4.75), 10000, risk_factor)
risk_factor.set_time_grid(time_grid)
risk_factor_vals = np.linspace(-0.2, 0.2, num_paths)
risk_factor_paths = np.repeat(risk_factor_vals.reshape(-1, 1), len(time_grid.grid), axis=1)
mtm_paths = portfolio.generate_paths(risk_factor_paths)

risk_factor_pdf_vals        = np.zeros((num_paths, len(time_grid.grid)))
risk_factor_pdf_vals[:, 1:] = norm.pdf(risk_factor_vals, loc=risk_factor_mean(time_grid.grid[1:], risk_factor).reshape(-1, 1), scale=np.sqrt(risk_factor_variance(time_grid.grid[1:], risk_factor)).reshape(-1, 1)).T
risk_factor_pdf_vals[:, 0]  = 0

In [84]:
plt.close('all')
fig, ax = plt.subplots(1, 1, figsize=(8, 4))
u = ax.plot(risk_factor_vals, mtm_paths[:, 0], label='$u(t, r)$')[0]
v = ax.plot(risk_factor_vals, risk_factor_pdf_vals[:, 0], label='pdf of $r_t$')[0]
rtime_grid = time_grid.grid[::2]
rmtm_paths = mtm_paths[:, ::2]
rpdf_vals = risk_factor_pdf_vals[:, ::2] * 10
ax.set_title(f"t = {rtime_grid[0]:.2f}")
ax.grid()
ax.set_xlabel("$r$")
ax.set_ylim(np.min(rmtm_paths), np.max(rmtm_paths))

def update(n):
    u.set_ydata(rmtm_paths[:, n])
    v.set_ydata(rpdf_vals[:, n] * 10)
    ax.set_title(f"t = {rtime_grid[n]:.2f}")
    return [u]

video = animation.FuncAnimation(fig, update, frames=len(rtime_grid), blit=True, interval=100, repeat=False)
plt.close(fig)
HTML(video.to_jshtml())